In [ ]:
import numpy as np
import pandas as pd
import scanpy as sc
import seaborn as sns
import scipy

In [ ]:
sc.settings.verbosity = 3             # verbosity: errors (0), warnings (1), info (2), hints (3)
sc.logging.print_versions()
sc.settings.set_figure_params(dpi=300, facecolor='white')

In [ ]:
results_file = 'RA_results.txt'  # the file that will store the analysis results

In [ ]:
adata = sc.read_csv(filename='input_data/RA_scanpy_counts.csv')

In [ ]:
adata

In [ ]:
sc.pl.highest_expr_genes(adata, n_top=20, )

In [ ]:
sc.pp.normalize_total(adata, target_sum=1e4)

In [ ]:
sc.pp.log1p(adata)

In [ ]:
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5)

In [ ]:
sc.pl.highly_variable_genes(adata)

In [ ]:
adata = adata[:, adata.var.highly_variable]

In [ ]:
sc.pp.scale(adata, max_value=10)

In [ ]:
sc.tl.pca(adata, svd_solver='arpack')

In [ ]:
adata.var_names

In [ ]:
sc.pl.pca_variance_ratio(adata, log=False)

In [ ]:
adata.write(results_file)

In [ ]:
adata

In [ ]:
sc.pp.neighbors(adata, n_neighbors=10, n_pcs=20)

In [ ]:
sc.tl.umap(adata)

In [ ]:
sc.pl.umap(adata, color = "SDC1")

In [ ]:
sc.tl.leiden(adata)

In [ ]:
sc.pl.umap(adata, color=['leiden'])

In [ ]:
adata.write(results_file)

In [ ]:
adata

In [ ]:
# Extract PCA projection for SI computation
pca_data = adata.obsm['X_pca']
np.savetxt("scanpy_RA_pca.csv", pca_data, delimiter = ",")

In [ ]:
anno = pd.read_csv('input_data/RA_scanpy_metadata.csv')

In [ ]:
anno

In [ ]:
adata.obs = anno

In [ ]:
scanpy_umap = sc.pl.umap(adata, color=['Type'])


In [ ]:
results_file = "RA_results.txt"

In [ ]:
adata.write(results_file)

In [ ]:
# Data integration using scanorama
import scanorama


In [ ]:
adata_list = []
unique_plates = anno['Plate'].unique()

In [ ]:
for plate in unique_plates:
    print(plate)
    adata_list.append(sc.read_csv(filename='input_data/scanpy_RA_{}_counts.csv'.format(plate)))

In [ ]:
# Integration.
integrated = scanorama.integrate_scanpy(adata_list)


In [ ]:
# Batch correction.
corrected = scanorama.correct_scanpy(adata_list)


In [ ]:
corrected

In [ ]:
# Integration and batch correction.
integrated, corrected = scanorama.correct_scanpy(adata_list, return_dimred=True)

In [ ]:
integrated[1].shape

In [ ]:
for i in range(0,25):
    np.savetxt('scanorama_RA_{}_dimred.csv'.format(unique_plates[i]), integrated[i], delimiter = ",")